# Preparation

In [ ]:
# expand folder

# ROOT_DIR = "/content/drive/MyDrive/Colab Notebooks"
# import os

# for i in os.listdir(ROOT_DIR+"/dataset/Kitti"):
#   if(len(i)==1):
#     os.mkdir(ROOT_DIR+"/dataset/Kitti/"+i+"_depth")
#     os.mkdir(ROOT_DIR+"/dataset/Kitti/"+i+"_pcd")
#     os.mkdir(ROOT_DIR+"/dataset/Kitti/"+i+"_rois")

    

In [ ]:
%pip install open3d
%pip install yacs
%pip install opencv-python
%pip install plotly


# Unprojection

### Function defined

In [ ]:
import numpy as np

def pixel_coord_np(width, height):
    """
    Pixel in homogenous coordinate
    Returns:
        Pixel coordinate:       [3, width * height]
    """
    x = np.linspace(0, width - 1, width).astype(np.int)
    y = np.linspace(0, height - 1, height).astype(np.int)
    [x, y] = np.meshgrid(x, y)
    return np.vstack((x.flatten(), y.flatten(), np.ones_like(x.flatten())))


def intrinsic_from_fov(height, width, fov=90):
    """
    Basic Pinhole Camera Model
    intrinsic params from fov and sensor width and height in pixels
    Returns:
        K:      [4, 4]
    """
    px, py = (width / 2, height / 2)
    hfov = fov / 360. * 2. * np.pi
    fx = width / (2. * np.tan(hfov / 2.))

    vfov = 2. * np.arctan(np.tan(hfov / 2) * height / width)
    fy = height / (2. * np.tan(vfov / 2.))

    return np.array([[fx, 0, px, 0.],
                     [0, fy, py, 0.],
                     [0, 0, 1., 0.],
                     [0., 0., 0., 1.]])
    
def draw_geometries(geometries):
    graph_objects = []

    for geometry in geometries:
        geometry_type = geometry.get_geometry_type()
        
        if geometry_type == o3d.geometry.Geometry.Type.PointCloud:
            points = np.asarray(geometry.points)
            colors = None
            if geometry.has_colors():
                colors = np.asarray(geometry.colors)
            elif geometry.has_normals():
                colors = (0.5, 0.5, 0.5) + np.asarray(geometry.normals) * 0.5
            else:
                # geometry.paint_uniform_color((1.0, 0.0, 0.0))
                # colors = np.asarray(geometry.colors)
                colors = np.asarray(geometry.colors)

            scatter_3d = go.Scatter3d(x=points[:,0], y=points[:,1], z=points[:,2], mode='markers', marker=dict(size=1, color=colors))
            graph_objects.append(scatter_3d)

        # if geometry_type == o3d.geometry.Geometry.Type.TriangleMesh:
        #     triangles = np.asarray(geometry.triangles)
        #     vertices = np.asarray(geometry.vertices)
        #     colors = None
        #     if geometry.has_triangle_normals():
        #         colors = (0.5, 0.5, 0.5) + np.asarray(geometry.triangle_normals) * 0.5
        #         colors = tuple(map(tuple, colors))
        #     else:
        #         colors = (1.0, 0.0, 0.0)
            
        #     mesh_3d = go.Mesh3d(x=vertices[:,0], y=vertices[:,1], z=vertices[:,2], i=triangles[:,0], j=triangles[:,1], k=triangles[:,2], facecolor=colors, opacity=0.50)
        #     graph_objects.append(mesh_3d)
        
    fig = go.Figure(
        data=graph_objects,
        layout=dict(
            scene=dict(
                xaxis=dict(visible=True),
                yaxis=dict(visible=True),
                zaxis=dict(visible=True)
            )
        )
    )
    fig.show()



def project_topview(cam_points):
    """
    Draw the topview projection
    """
    max_longitudinal = 70
    window_x = (-50, 50)
    window_y = (-3, max_longitudinal)

    x, y, z = cam_points
    # flip the y-axis to positive upwards
    y = - y

    # We sample points for points less than 70m ahead and above ground
    # Camera is mounted 1m above on an ego vehicle
    ind = np.where((z < max_longitudinal) & (y > -1.2))
    bird_eye = cam_points[:3, ind]

    # Color by radial distance
    dists = np.sqrt(np.sum(bird_eye[0:2:2, :] ** 2, axis=0))
    axes_limit = 10
    colors = np.minimum(1, dists / axes_limit / np.sqrt(2))

    # Draw Points
    fig, axes = plt.subplots(figsize=(12, 12))
    axes.scatter(bird_eye[0, :], bird_eye[2, :], c=colors, s=0.1)
    axes.set_xlim(window_x)
    axes.set_ylim(window_y)
    axes.set_title('Bird Eye View')
    plt.axis('off')

    plt.gca().set_aspect('equal')
    plt.show()

### Prepare Point cloud

In [ ]:
import cv2
import matplotlib.pyplot as plt
import numpy as np
import open3d as o3d
from math import sin,cos,pi
import plotly.graph_objects as go
import os
import matplotlib.pyplot as plt
from mpl_toolkits import mplot3d
from PIL import Image

import sys
sys.path.append("../packnet-sfm/")

from packnet_sfm.datasets.augmentations import resize_image
from packnet_sfm.utils.depth import load_depth
'''
depth = []
rgb = [] 
f = open("../Kitti/3_pose/pose.json")
pose = json.load(f)
intrinsics = np.loadtxt("../Kitti/3_pose/intrinsic.txt")

for filename in os.listdir(data_path):
    img = cv2.imread('../Kitti/3/'+filename)
    img = np.array(resize_image(Image.fromarray(cv2.cvtColor(img, cv2.COLOR_BGR2RGB)), (384,1280)))
    depth.append(load_depth('../Kitti/3_depth/' + filename[:-3]+"npz"))
    rgb.append(np.array(cv2.cvtColor(img,cv2.COLOR_BGR2RGB)))


'''

# -------------------------------------------------------------
datapath = "../Kitti/"
imgname  = []

for i in os.listdir(datapath):
  if len(i) == 1:
    imgname.append(i)

raw_pcd = []

for i in os.listdir(datapath+"3"):
  imgpath   = datapath + "3/" + i 
  depthpath = datapath + "3_depth/" + i[:-3] + "npz"
  
  img = cv2.imread(imgpath)
  img = np.array(resize_image(Image.fromarray(cv2.cvtColor(img, cv2.COLOR_BGR2RGB)), (384,1280)))

  # Load images
  rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)

  # Depth is stored as float32 in meters
  depth =load_depth(depthpath)

  # Get intrinsic parameters
  height, width, _ = rgb.shape

  K = np.loadtxt("../Kitti/3_pose/intrinsic.txt")

  K_inv = np.linalg.inv(K)

  # Get pixel coordinates homogeneous
  pixel_coords = pixel_coord_np(width, height)  # [3, npoints]

  # Apply back-projection: K_inv @ pixels * depth
  cam_coords = K_inv[:3, :3] @ pixel_coords * depth.flatten()
  print(cam_coords.shape)
  
  # 
  # Limit points to 150m in the z-direction for visualisation
  # ind = np.where((cam_coords[0] <= 3000)==(cam_coords[0]>-4000))[0]
  # cam_coords = cam_coords[:, ind]
  # colors = np.vstack((rgb[:,:,0].flatten()[ind], rgb[:,:,1].flatten()[ind], rgb[:,:,2].flatten()[ind])).transpose()
  colors = np.vstack((rgb[:,:,0].flatten(), rgb[:,:,1].flatten(), rgb[:,:,2].flatten())).transpose()

  # Visualize
  pcd_cam = o3d.geometry.PointCloud()
  pcd_cam.points = o3d.utility.Vector3dVector(cam_coords.T[:, :3])
  pcd_cam.colors = o3d.utility.Vector3dVector(colors/255)

  # print(cam_coords[0][:5])
  # print(len(pcd_cam.points[0]))
  # Flip it, otherwise the pointcloud will be upside down
  pcd_cam.transform([[1, 0, 0, 0], [0, -1, 0, 0], [0, 0, -1, 0], [0, 0, 0, 1]])

  # wrtie point cloud
  o3d.io.write_point_cloud(datapath + "3_pcd/" + i[:-3] +"pcd",pcd_cam)
  
  # o3d.visualization.draw_geometries=draw_geometries
  # o3d.visualization.draw_geometries([pcd_cam])
  raw_pcd.append(pcd_cam)
 
  # Do top view projection
  # project_topview(cam_coords)

In [2]:
import cv2
import matplotlib.pyplot as plt
import numpy as np
import open3d as o3d
from math import sin,cos,pi
import plotly.graph_objects as go
import os
import matplotlib.pyplot as plt
from mpl_toolkits import mplot3d
from PIL import Image

import sys
sys.path.append("../packnet-sfm/")

from packnet_sfm.datasets.augmentations import resize_image
from packnet_sfm.utils.depth import load_depth

In [12]:
path = "../Kitti/3/"
depthpath = "../Kitti/3_depth/"
filenames = os.listdir(path)
for i in range(len(filenames)):
    filenames[i] = filenames[i][:-3]+'npz'
d = load_depth(depthpath+filenames[0])


In [13]:
d.shape

(384, 1280)

In [ ]:
o3d.visualization.draw_geometries([raw_pcd[0]])

## Global Registration

In [ ]:
import copy
# o3d.visualization.draw_geometries=draw_geometries

# p = o3d.io.read_point_cloud("/content/drive/My Drive/Colab Notebooks/dataset/Kitti/1_pcd/0000000000.pcd")
# print(np.asarray(p.colors))

def preprocess_point_cloud(pcd, voxel_size):
  print(":: Downsample with a voxel size %.3f." % voxel_size)
  pcd_down = pcd.voxel_down_sample(voxel_size)

  radius_normal = voxel_size * 2
  print(":: Estimate normal with search radius %.3f." % radius_normal)
  pcd_down.estimate_normals(
      o3d.geometry.KDTreeSearchParamHybrid(radius=radius_normal, max_nn=30))

  radius_feature = voxel_size * 5
  print(":: Compute FPFH feature with search radius %.3f." % radius_feature)
  pcd_fpfh = o3d.pipelines.registration.compute_fpfh_feature(
      pcd_down,
      o3d.geometry.KDTreeSearchParamHybrid(radius=radius_feature, max_nn=100))
  return pcd_down, pcd_fpfh

voxel_size = 0.005
pcd_down,pcd_fpfh = [],[]

for i in pcd:
  down,fpfh = preprocess_point_cloud(i,voxel_size)
  pcd_down.append(down)
  pcd_fpfh.append(fpfh)


In [ ]:
o3d.visualization.draw_geometries([pcd_down[0]])

In [ ]:
# print(np.asarray(pcd[0].points).shape)
# print(np.asarray(pcd_down[0]).shape)
print((pcd_fpfh[0].data))


In [ ]:
# computer global_registration
def execute_global_registration(source_down, target_down, source_fpfh,
                                target_fpfh, voxel_size):
    distance_threshold = voxel_size * 0.5
    print(":: Apply fast global registration with distance threshold %.3f" \
            % distance_threshold)
    result = o3d.pipelines.registration.registration_fgr_based_on_feature_matching(
        source_down, target_down, source_fpfh, target_fpfh,
        o3d.pipelines.registration.FastGlobalRegistrationOption(
            maximum_correspondence_distance=distance_threshold))
    return result

res = execute_global_registration(pcd_down[1],pcd_down[0],pcd_fpfh[1],pcd_fpfh[0],voxel_size)
# res.append(execute_global_registration(pcd_down[1],pcd_down[0],pcd_fpfh[1],pcd_fpfh[0],voxel_size))
# for i in range(2,len(pcd_down)):
#   res.append(execute_global_registration(pcd_down[i].transform(res[i-1].transformation),pcd_down[0],pcd_fpfh[1],pcd_fpfh[0],voxel_size))


## Result Visualize

### Rotate

In [ ]:
# Rotate X
alpha = pi/6
R = pcd_cam.get_rotation_matrix_from_xyz((alpha, 0, 0))
pcd_cam.rotate(R, center=(0,0,0))
points=np.asarray(pcd_cam.points)

In [ ]:
# Rotate Y
thetha = -pi/10
R = pcd_cam.get_rotation_matrix_from_xyz((0, thetha, 0))
pcd_cam.rotate(R, center=(0,0,0))
points=np.asarray(pcd_cam.points)


In [ ]:
# Rotate Z
gamma = pi/12
R = pcd_cam.get_rotation_matrix_from_xyz((0, 0, gamma))
pcd_cam.rotate(R, center=(0,0,0))
points=np.asarray(pcd_cam.points)


### visualize

In [ ]:
import matplotlib.pyplot as plt
from mpl_toolkits import mplot3d
import time

plt.figure(figsize=(25,25))
ax = plt.axes(projection='3d')
# ax.zaxis.set_rotate_label(False) 
ax.view_init(elev=0,azim=10)
ax.axis("on")
ax.set_xlabel('$X$', fontsize=20)
ax.set_ylabel('$Y$')
ax.set_zlabel('$Z$', fontsize=30)

points=np.asarray(pcd[0].points)
colors=np.asarray(pcd[0].colors)

# ind = np.where((points[:,1]<5000)==(points[:,0]<2000))[0]

ax.scatter(points[:,2], points[:,0], points[:,1], s=15, c=colors,marker='s')

# ax.yticks(np.arrange(points[:,2].min(),points[:,2].max(),0.5))
# plt.savefig(DATA_PATH+)

# from IPython.display import clear_output  

# for angle in range(0,360):
#     ax.view_init(elev=5,azim=angle,vertical_axis='y')
#     ax.scatter(points[:,0], points[:,1], points[:,2], s=1, c=colors/255)
#     plt.show()
#     clear_output(wait=True)
#     time.sleep(0.01)

In [ ]:
len(ind[0])

# Plotly

In [ ]:
import plotly.graph_objects as go

dists = np.sqrt(np.sum(cam_coords[0:2:2, :] ** 2, axis=0))
axes_limit = 10
colors = np.minimum(1, dists / axes_limit / np.sqrt(2))

fig = go.Figure(
    data=[
        go.Scatter3d(
            x=cam_coords[0], y=cam_coords[1], z=cam_coords[2], 
            mode='markers',
            marker=dict(size=1, color=colors)
        )
    ],
    layout=dict(
        scene=dict(
            xaxis=dict(visible=False),
            yaxis=dict(visible=False),
            zaxis=dict(visible=False)
        )
    )
)
fig.show()

# Pypotree

In [ ]:
%pip install pypotree
import pypotree 
cloud = np.asarray(pcd_cam.points)
#xyz = np.random.random((100000,3)) #working
cloudpath = pypotree.generate_cloud_for_display(cloud)
pypotree.display_cloud_colab(cloudpath)

# CamViz